# Spark Streaming
This notebook takes in the `gemini-feed` Kafka topic and produces to the `spark.out` topic a feed which includes the order price volume ratio and bid/ask liquidity for BTC.

In [1]:
# !pip install --force-reinstall pyspark==2.4.6

In [2]:
from kafka import KafkaProducer
import os  
os.environ['PYSPARK_SUBMIT_ARGS'] = '--packages org.apache.spark:spark-streaming-kafka-0-8_2.11:2.0.2 pyspark-shell'  

In [3]:
producer = KafkaProducer(bootstrap_servers='localhost:9092')

In [4]:
from pyspark import SparkContext
from pyspark.streaming import StreamingContext
from pyspark.streaming.kafka import KafkaUtils  
from kafka import KafkaProducer
import json
import time

In [5]:
sc = SparkContext(appName="PythonSparkStreamingKafka_RM_01")  
sc.setLogLevel("ERROR") 
ssc = StreamingContext(sc, 60)  

In [6]:
kafkaStream = KafkaUtils.createStream(ssc, 'localhost:2181', 'spark-streaming', {'gemini-feed':1})  

In [7]:
parsed = kafkaStream.map(lambda v: json.loads(v[1]))

In [8]:
def handler(message):
    records = message.collect()
    for record in records:
        output = {}
        output['type'] = record[0]
        output['value'] = record[1]
        output['timestamp'] = int(time.time())
        producer.send('spark.out', bytes(json.dumps(output), 'utf-8'))
        producer.flush()

In [9]:
def price_volume(x):
    price = float(x['price'])
    remaining = float(x['remaining'])
    x['price_volume'] = price * remaining
    return (x['side'], x['price_volume'])

In [10]:
parsed_pv = parsed.map(lambda x: price_volume(x))

In [11]:
grouped = parsed_pv.reduceByKey(lambda accum, n: accum + n)

In [12]:
grouped_sorted = grouped.transform(lambda rdd: rdd.sortByKey())

In [13]:
grouped_sorted.foreachRDD(handler)

In [14]:
results = grouped_sorted.map(lambda x: ('price_volume', x[1]))

In [15]:
ratio = results.reduceByKey(lambda x, y: x/y)

In [16]:
ratio.foreachRDD(handler)

In [17]:
grouped_sorted.pprint()
ratio.pprint()

In [18]:
ssc.start()

In [19]:
ssc.stop()

In [20]:
# from kafka import KafkaProducer, KafkaConsumer

In [21]:
# producer = KafkaProducer(bootstrap_servers='localhost:9092')

In [25]:
# consumer = KafkaConsumer('gemini-feed',
#                          bootstrap_servers=['localhost:9092'],
#                          auto_offset_reset='earliest',
#                          enable_auto_commit=True,
#                         value_deserializer=lambda x: x.decode('utf-8')
# )

In [27]:
# for message in consumer:
#     print(message)

ConsumerRecord(topic='gemini-feed', partition=0, offset=1, timestamp=1602623330613, timestamp_type=0, key=None, value='{"side": "bid", "price": "0.02", "remaining": "30960", "price_volume": "1"}', headers=[], checksum=2672202781, serialized_key_size=-1, serialized_value_size=75, serialized_header_size=-1)
ConsumerRecord(topic='gemini-feed', partition=0, offset=2, timestamp=1602623330614, timestamp_type=0, key=None, value='{"side": "bid", "price": "0.04", "remaining": "0.00055", "price_volume": "1"}', headers=[], checksum=2356585512, serialized_key_size=-1, serialized_value_size=77, serialized_header_size=-1)
ConsumerRecord(topic='gemini-feed', partition=0, offset=3, timestamp=1602623330615, timestamp_type=0, key=None, value='{"side": "bid", "price": "0.05", "remaining": "7494", "price_volume": "1"}', headers=[], checksum=4182436564, serialized_key_size=-1, serialized_value_size=74, serialized_header_size=-1)
ConsumerRecord(topic='gemini-feed', partition=0, offset=4, timestamp=160262333

ConsumerRecord(topic='gemini-feed', partition=0, offset=1817, timestamp=1602623331142, timestamp_type=0, key=None, value='{"side": "bid", "price": "9011.00", "remaining": "0.22195094", "price_volume": "1"}', headers=[], checksum=3907689206, serialized_key_size=-1, serialized_value_size=83, serialized_header_size=-1)
ConsumerRecord(topic='gemini-feed', partition=0, offset=1818, timestamp=1602623331142, timestamp_type=0, key=None, value='{"side": "bid", "price": "9012.00", "remaining": "0.02774079", "price_volume": "1"}', headers=[], checksum=2110497831, serialized_key_size=-1, serialized_value_size=83, serialized_header_size=-1)
ConsumerRecord(topic='gemini-feed', partition=0, offset=1819, timestamp=1602623331142, timestamp_type=0, key=None, value='{"side": "bid", "price": "9012.29", "remaining": "0.00179", "price_volume": "1"}', headers=[], checksum=609570054, serialized_key_size=-1, serialized_value_size=80, serialized_header_size=-1)
ConsumerRecord(topic='gemini-feed', partition=0, o

ConsumerRecord(topic='gemini-feed', partition=0, offset=3317, timestamp=1602623331551, timestamp_type=0, key=None, value='{"side": "bid", "price": "10978.00", "remaining": "0.04563672", "price_volume": "1"}', headers=[], checksum=3167175607, serialized_key_size=-1, serialized_value_size=84, serialized_header_size=-1)
ConsumerRecord(topic='gemini-feed', partition=0, offset=3318, timestamp=1602623331551, timestamp_type=0, key=None, value='{"side": "bid", "price": "10978.18", "remaining": "0.00768561", "price_volume": "1"}', headers=[], checksum=2064723352, serialized_key_size=-1, serialized_value_size=84, serialized_header_size=-1)
ConsumerRecord(topic='gemini-feed', partition=0, offset=3319, timestamp=1602623331551, timestamp_type=0, key=None, value='{"side": "bid", "price": "10978.59", "remaining": "0.001", "price_volume": "1"}', headers=[], checksum=3883370381, serialized_key_size=-1, serialized_value_size=79, serialized_header_size=-1)
ConsumerRecord(topic='gemini-feed', partition=0,

ConsumerRecord(topic='gemini-feed', partition=0, offset=4816, timestamp=1602623331950, timestamp_type=0, key=None, value='{"side": "ask", "price": "14387.00", "remaining": "0.01", "price_volume": "1"}', headers=[], checksum=3641428912, serialized_key_size=-1, serialized_value_size=78, serialized_header_size=-1)
ConsumerRecord(topic='gemini-feed', partition=0, offset=4817, timestamp=1602623331950, timestamp_type=0, key=None, value='{"side": "ask", "price": "14388.00", "remaining": "1", "price_volume": "1"}', headers=[], checksum=1211460311, serialized_key_size=-1, serialized_value_size=75, serialized_header_size=-1)
ConsumerRecord(topic='gemini-feed', partition=0, offset=4818, timestamp=1602623331950, timestamp_type=0, key=None, value='{"side": "ask", "price": "14390.00", "remaining": "1", "price_volume": "1"}', headers=[], checksum=723165411, serialized_key_size=-1, serialized_value_size=75, serialized_header_size=-1)
ConsumerRecord(topic='gemini-feed', partition=0, offset=4819, timest

ConsumerRecord(topic='gemini-feed', partition=0, offset=6316, timestamp=1602623400473, timestamp_type=0, key=None, value='{"side": "bid", "price": "11454.95", "remaining": "0.03745609", "price_volume": "1"}', headers=[], checksum=650635428, serialized_key_size=-1, serialized_value_size=84, serialized_header_size=-1)
ConsumerRecord(topic='gemini-feed', partition=0, offset=6317, timestamp=1602623400476, timestamp_type=0, key=None, value='{"side": "bid", "price": "11454.95", "remaining": "0.02709116", "price_volume": "1"}', headers=[], checksum=3966359242, serialized_key_size=-1, serialized_value_size=84, serialized_header_size=-1)
ConsumerRecord(topic='gemini-feed', partition=0, offset=6318, timestamp=1602623400479, timestamp_type=0, key=None, value='{"side": "bid", "price": "11454.95", "remaining": "0.03616015", "price_volume": "1"}', headers=[], checksum=4022181987, serialized_key_size=-1, serialized_value_size=84, serialized_header_size=-1)
ConsumerRecord(topic='gemini-feed', partitio

...

ConsumerRecord(topic='gemini-feed', partition=0, offset=17260, timestamp=1602624721639, timestamp_type=0, key=None, value='{"side": "ask", "price": "15497.51", "remaining": "0.645", "price_volume": "1"}', headers=[], checksum=2607292281, serialized_key_size=-1, serialized_value_size=79, serialized_header_size=-1)
ConsumerRecord(topic='gemini-feed', partition=0, offset=17261, timestamp=1602624721641, timestamp_type=0, key=None, value='{"side": "ask", "price": "15499.91", "remaining": "5", "price_volume": "1"}', headers=[], checksum=2546073109, serialized_key_size=-1, serialized_value_size=75, serialized_header_size=-1)
ConsumerRecord(topic='gemini-feed', partition=0, offset=17262, timestamp=1602624721641, timestamp_type=0, key=None, value='{"side": "ask", "price": "15500.00", "remaining": "1.41002602", "price_volume": "1"}', headers=[], checksum=4156251593, serialized_key_size=-1, serialized_value_size=84, serialized_header_size=-1)
ConsumerRecord(topic='gemini-feed', partition=0, offse

ConsumerRecord(topic='gemini-feed', partition=0, offset=17594, timestamp=1602624721855, timestamp_type=0, key=None, value='{"side": "ask", "price": "22987.00", "remaining": "0.5", "price_volume": "1"}', headers=[], checksum=3558184276, serialized_key_size=-1, serialized_value_size=77, serialized_header_size=-1)
ConsumerRecord(topic='gemini-feed', partition=0, offset=17595, timestamp=1602624721855, timestamp_type=0, key=None, value='{"side": "ask", "price": "23000.00", "remaining": "2.12173914", "price_volume": "1"}', headers=[], checksum=2657009923, serialized_key_size=-1, serialized_value_size=84, serialized_header_size=-1)
ConsumerRecord(topic='gemini-feed', partition=0, offset=17596, timestamp=1602624721856, timestamp_type=0, key=None, value='{"side": "ask", "price": "23053.00", "remaining": "0.0056478", "price_volume": "1"}', headers=[], checksum=2729147569, serialized_key_size=-1, serialized_value_size=83, serialized_header_size=-1)
ConsumerRecord(topic='gemini-feed', partition=0,

ConsumerRecord(topic='gemini-feed', partition=0, offset=17859, timestamp=1602624722212, timestamp_type=0, key=None, value='{"side": "ask", "price": "11476.00", "remaining": "1.91", "price_volume": "1"}', headers=[], checksum=3203268251, serialized_key_size=-1, serialized_value_size=78, serialized_header_size=-1)
ConsumerRecord(topic='gemini-feed', partition=0, offset=17860, timestamp=1602624723344, timestamp_type=0, key=None, value='{"side": "bid", "price": "11306.73", "remaining": "0.45698714", "price_volume": "1"}', headers=[], checksum=317969753, serialized_key_size=-1, serialized_value_size=84, serialized_header_size=-1)
ConsumerRecord(topic='gemini-feed', partition=0, offset=17861, timestamp=1602624723486, timestamp_type=0, key=None, value='{"side": "ask", "price": "11457.12", "remaining": "5.37666071", "price_volume": "1"}', headers=[], checksum=1839030431, serialized_key_size=-1, serialized_value_size=84, serialized_header_size=-1)
ConsumerRecord(topic='gemini-feed', partition=0

ConsumerRecord(topic='gemini-feed', partition=0, offset=17887, timestamp=1602624725385, timestamp_type=0, key=None, value='{"side": "bid", "price": "11457.11", "remaining": "0.01501094", "price_volume": "1"}', headers=[], checksum=3477158476, serialized_key_size=-1, serialized_value_size=84, serialized_header_size=-1)
ConsumerRecord(topic='gemini-feed', partition=0, offset=17888, timestamp=1602624725538, timestamp_type=0, key=None, value='{"side": "ask", "price": "11476.00", "remaining": "0", "price_volume": "1"}', headers=[], checksum=3326762264, serialized_key_size=-1, serialized_value_size=75, serialized_header_size=-1)
ConsumerRecord(topic='gemini-feed', partition=0, offset=17889, timestamp=1602624726074, timestamp_type=0, key=None, value='{"side": "bid", "price": "11434.23", "remaining": "0.99235243", "price_volume": "1"}', headers=[], checksum=1868168898, serialized_key_size=-1, serialized_value_size=84, serialized_header_size=-1)
ConsumerRecord(topic='gemini-feed', partition=0, 

KeyboardInterrupt: 

In [ ]:
from kafka import KafkaProducer
import os  
os.environ['PYSPARK_SUBMIT_ARGS'] = '--packages org.apache.spark:spark-streaming-kafka-0-8_2.11:2.0.2 pyspark-shell' 
producer = KafkaProducer(bootstrap_servers='localhost:9092')
from pyspark import SparkContext
from pyspark.streaming import StreamingContext
from pyspark.streaming.kafka import KafkaUtils  
from kafka import KafkaProducer
import json
import time

sc = SparkContext(appName="PythonSparkStreamingKafka_RM_01")  
sc.setLogLevel("ERROR") 
ssc = StreamingContext(sc, 60)  

kafkaStream = KafkaUtils.createStream(ssc, 'localhost:2181', 'spark-streaming', {'gemini-feed':1}) 
parsed = kafkaStream.map(lambda v: json.loads(v[1]))

def handler(message):
    records = message.collect()
    for record in records:
        output = {}
        output['type'] = record[0]
        output['value'] = record[1]
        output['timestamp'] = int(time.time())
        producer.send('spark.out', bytes(json.dumps(output), 'utf-8'))
        producer.flush()
        
def price_volume(x):
    price = float(x['price'])
    remaining = float(x['remaining'])
    x['price_volume'] = price * remaining
    return (x['side'], x['price_volume'])

parsed_pv = parsed.map(lambda x: price_volume(x))
grouped = parsed_pv.reduceByKey(lambda accum, n: accum + n)
grouped_sorted = grouped.transform(lambda rdd: rdd.sortByKey())
grouped_sorted.foreachRDD(handler)
results = grouped_sorted.map(lambda x: ('price_volume', x[1]))
ratio = results.reduceByKey(lambda x, y: x/y)
ratio.foreachRDD(handler)
grouped_sorted.pprint()
ratio.pprint()
ssc.start()